In [1]:
import pandas as pd
import numpy as np
import pickle
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.grid_search import GridSearchCV

C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\grid_search.py:42: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [2]:
from openpyxl import Workbook,load_workbook

In [3]:
import os

In [4]:
from sklearn.metrics import r2_score,mean_squared_error,precision_score,recall_score,accuracy_score,confusion_matrix,roc_auc_score

In [17]:
os.chdir('../output_data')

In [18]:
df = pd.read_csv('oot.csv',header=0)

FileNotFoundError: File b'oot.csv' does not exist

In [7]:
ignore_cols = ['Symbol','Series','Date','Prev_Close','Open','Close','Prev_Close_min','Prev_Close_max','Sector']

In [20]:
os.chdir('../pickles')

In [10]:
prob_lr_columns = df.drop(ignore_cols+['actual_return','lift'],axis=1).columns

In [12]:
pickle.dump(prob_lr_columns,open('prob_lr_columns.pickle','wb'))

In [21]:
numerical = pickle.load(open('numerical.pickle','rb'))
categorical = pickle.load(open('categorical.pickle','rb'))
conversion_dict = pickle.load(open('conversion_dict.pickle','rb'))
imputation_cols = pickle.load(open('imputation_cols.pickle','rb'))
model_columns = pickle.load(open('model_columns.pickle','rb'))
lr_model_columns = pickle.load(open('lr_model_columns.pickle','rb'))
order = pickle.load(open('order.pickle','rb'))
pca = pickle.load(open('pca.pickle','rb'))
scale = pickle.load(open('scale.pickle','rb'))
prob_lr_columns = pickle.load(open('prob_lr_columns.pickle','rb'))

In [22]:
model_columns = prob_lr_columns

In [23]:
from keras.layers import Input,Dense,Dropout

Using TensorFlow backend.


In [24]:
from keras.models import Model
from keras.optimizers import Adam,RMSprop

In [25]:
len(model_columns)

37

In [15]:
states = Input(shape=(37,))
x = Dense(units = 20, activation='linear')(states)
y = Dense(units = 20,activation='linear')(x)
q_value = Dense(units = 1,activation='sigmoid')(y)
ann_model = Model(inputs=states,outputs=q_value)
ann_model.compile(loss='binary_crossentropy',optimizer=Adam(lr=.001))

In [16]:
model_inputs = np.array(df.drop(ignore_cols+['actual_return','lift'],axis=1))
model_returns = np.array(df['lift'])

In [17]:
ann_model.fit(model_inputs,model_returns,epochs=100,batch_size=50)

Epoch 1/100
85799/85799 [==============================] - 3s 37us/step - loss: 0.6920
Epoch 2/100
85799/85799 [==============================] - 2s 26us/step - loss: 0.6911
Epoch 3/100
85799/85799 [==============================] - 2s 26us/step - loss: 0.6910
Epoch 4/100
85799/85799 [==============================] - 2s 26us/step - loss: 0.6908
Epoch 5/100
85799/85799 [==============================] - 2s 27us/step - loss: 0.6904
Epoch 6/100
85799/85799 [==============================] - 2s 29us/step - loss: 0.6903
Epoch 7/100
85799/85799 [==============================] - 2s 28us/step - loss: 0.6902
Epoch 8/100
85799/85799 [==============================] - 2s 27us/step - loss: 0.6901
Epoch 9/100
85799/85799 [==============================] - 3s 29us/step - loss: 0.6901
Epoch 10/100
85799/85799 [==============================] - 2s 27us/step - loss: 0.6900
Epoch 11/100
85799/85799 [==============================] - 2s 27us/step - loss: 0.6900
Epoch 12/100
85799/85799 [===============

In [26]:
os.chdir('../Models/')

In [19]:
ann_model.save('ann_prob_model_lr.h5')

In [27]:
from keras.models import load_model

In [28]:
model = load_model('ann_prob_model_lr.h5')

In [22]:
pred_returns = [x[0] for x in model.predict(model_inputs)]

In [23]:
roc_auc_score(y_score=pred_returns,y_true=model_returns)

0.5379750435803964

In [24]:
df['lift_prob'] = pred_returns

In [25]:
buck_rows = df.shape[0]//100
stats_numerical = pd.DataFrame()
for col in ['lift_prob']:
    df_append = df.sort_values(by=col,ascending=False)
    df_append.reset_index(inplace=True)
    df_append['bucket'] = df_append.index//buck_rows
    df_stats = df_append.groupby('bucket').agg({col:['min','mean','max','count'],
                                               'lift':['sum']})
    df_stats.columns = df_stats.columns.droplevel()
    df_stats.columns = ['min_prob','mean_prob','max_prob','counts','lifts']
    df_stats.reset_index(inplace=True)
    stats_numerical = stats_numerical.append(df_stats)

In [26]:
stats_numerical

bucket  min_prob  mean_prob  max_prob  counts  lifts
0         0  0.535330   0.544644  0.578660     857    506
1         1  0.527872   0.531185  0.535316     857    492
2         2  0.523329   0.525510  0.527871     857    491
3         3  0.519894   0.521521  0.523328     857    439
4         4  0.517077   0.518433  0.519886     857    448
5         5  0.514576   0.515798  0.517075     857    453
6         6  0.512573   0.513560  0.514570     857    447
7         7  0.510616   0.511568  0.512571     857    453
8         8  0.508959   0.509760  0.510614     857    451
9         9  0.507423   0.508201  0.508956     857    453
10       10  0.506113   0.506776  0.507421     857    436
11       11  0.504767   0.505447  0.506113     857    459
12       12  0.503494   0.504130  0.504763     857    458
13       13  0.502277   0.502881  0.503493     857    440
14       14  0.501154   0.501713  0.502275     857    429
15       15  0.500147   0.500633  0.501154     857    444
16       16  0.499132   0.499635  0.500145     857    432
17       17  0.498199   0.498665  0.499131     857    410
18       18  0.497301   0.497768  0.498198     857    438
19       19  0.496331   0.496820  0.497299     857    435
20       20  0.495431   0.495888  0.496331     857    415
21       21  0.494521   0.494985  0.495430     857    445
22       22  0.493646   0.494075  0.494520     857    429
23       23  0.492812   0.493215  0.493643     857    435
24       24  0.492007   0.492396  0.492812     857    417
25       25  0.491181   0.491597  0.492006     857    427
26       26  0.490398   0.490783  0.491178     857    424
27       27  0.489621   0.490017  0.490395     857    401
28       28  0.488876   0.489235  0.489620     857    410
29       29  0.488106   0.488482  0.488875     857    430
..      ...       ...        ...       ...     ...    ...
71       71  0.459530   0.459910  0.460272     857    404
72       72  0.458769   0.459163  0.459530     857    372
73       73  0.457993   0.458380  0.458767     857    391
74       74  0.457188   0.457597  0.457993     857    401
75       75  0.456350   0.456766  0.457186     857    379
76       76  0.455541   0.455949  0.456349     857    401
77       77  0.454721   0.455132  0.455540     857    385
78       78  0.453866   0.454287  0.454721     857    385
79       79  0.453018   0.453445  0.453865     857    353
80       80  0.452070   0.452554  0.453017     857    353
81       81  0.451088   0.451574  0.452069     857    350
82       82  0.450038   0.450561  0.451085     857    369
83       83  0.449024   0.449520  0.450036     857    366
84       84  0.447962   0.448482  0.449023     857    368
85       85  0.446787   0.447401  0.447961     857    334
86       86  0.445585   0.446180  0.446787     857    363
87       87  0.444343   0.444998  0.445583     857    351
88       88  0.442990   0.443683  0.444342     857    388
89       89  0.441500   0.442260  0.442985     857    360
90       90  0.439847   0.440691  0.441500     857    381
91       91  0.438183   0.439033  0.439846     857    375
92       92  0.436416   0.437283  0.438183     857    362
93       93  0.434211   0.435364  0.436416     857    386
94       94  0.431871   0.433084  0.434210     857    381
95       95  0.429212   0.430554  0.431861     857    372
96       96  0.425989   0.427653  0.429211     857    373
97       97  0.421856   0.424044  0.425988     857    346
98       98  0.415734   0.418983  0.421841     857    385
99       99  0.398616   0.409784  0.415697     857    362
100     100  0.378749   0.393761  0.398609      99     53

[101 rows x 6 columns]

In [27]:
os.chdir('../Statistics/')

In [28]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
stats_numerical.to_excel(writer,sheet_name='ann_prob_stats_lr',index=False)
writer.save()
writer.close()

In [29]:
os.chdir('../Input_Data')

In [30]:
df = pd.read_csv('oot.csv',header=0)

In [31]:
rename_dict = {col : col.replace('%','pct_') for col in df.columns if '%' in col}

In [32]:
df_val = df

In [33]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [34]:
df_val['lift'] = df_val['actual_return'].apply(lambda x: 1 if x >0 else 0) 

In [35]:
for col in categorical:
    for category in conversion_dict[col]:
        df_val[col+'_dum_'+str(category)] = 0
        df_val.loc[df_val[col]==category,col+'_dum_'+str(category)]=1
    print(col+' done')

Sector done


In [36]:
rename_dict = {col : col.replace(' ','_').replace('-','_').replace('&','_') for col in df.columns if '-' in col or ' ' in col}

In [37]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [38]:
for col in model_columns:
    df_val[col] = df_val[col].apply(lambda x : x if np.abs(x) <= 1 else np.sign(x)*1)

In [39]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 37)                0         
_________________________________________________________________
dense_1 (Dense)              (None, 20)                760       
_________________________________________________________________
dense_2 (Dense)              (None, 20)                420       
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 21        
Total params: 1,201
Trainable params: 1,201
Non-trainable params: 0
_________________________________________________________________


In [40]:
def get_equation(model):
    mat1 = np.matrix(model.layers[1].get_weights()[0])
    mat2 = np.matrix(model.layers[1].get_weights()[1])
    mat3 = np.concatenate((mat1,mat2),axis=0)
    mat4 = np.matrix(model.layers[2].get_weights()[0])
    mat5 = np.matmul(mat3,mat4)
    mat5[37,:]+=np.matrix(model.layers[2].get_weights()[1])
    mat6 = np.matrix(model.layers[3].get_weights()[0])
    mat7 = np.matmul(mat5,mat6)
    mat7[37,:]+=np.matrix(model.layers[3].get_weights()[1])
    
    return [float(x) for x in mat7[:,0]]

In [41]:
dynamic_eqn = pd.DataFrame()
dynamic_eqn['Variable'] = list(model_columns)+['intercept']
dynamic_eqn['eq0'] = get_equation(model)

In [42]:
model.predict(np.array(model_inputs[56,:]).reshape(1,37))[0][0]

0.46790403

In [43]:
z = np.dot(np.array(list(model_inputs[56,:])+[1]),np.array(get_equation(model)))

In [44]:
np.exp(z)/(1+np.exp(z))

0.46790404011477266

In [42]:
dates = sorted(list(df_val['Date'].unique()))

In [43]:
os.chdir('../Models/')

In [44]:
model = load_model('ann_prob_model_lr.h5')

In [45]:
ann_val_stats = pd.DataFrame()
for i,date in enumerate(dates):
    df_req = df_val[df_val['Date']==date]
    model_inputs = np.array(df_req[model_columns])
    model_returns = np.array(df_req['lift'])
    df_req['lift_prob'] = [x[0] for x in model.predict(model_inputs)]
    df_append = df_req[['Date','Symbol','Sector','lift','lift_prob']]
    ann_val_stats = ann_val_stats.append(df_append)
    model.fit(model_inputs,model_returns,batch_size=50,epochs=100)
    model.save('ann_prob_model_lr.h5')
    model = load_model('ann_prob_model_lr.h5')
    dynamic_eqn['eq'+str(i+1)] = get_equation(model)
    print('\n')
    print(dynamic_eqn)
    print('\n')
    print('{} days done'.format(i+1))
    print('\n')

C:\Users\DELL\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Epoch 1/100
50/50 [==============================] - 0s 7ms/step - loss: 0.8135
Epoch 2/100
50/50 [==============================] - 0s 40us/step - loss: 0.8139
Epoch 3/100
50/50 [==============================] - 0s 40us/step - loss: 0.8131
Epoch 4/100
50/50 [==============================] - 0s 60us/step - loss: 0.8114
Epoch 5/100
50/50 [==============================] - 0s 60us/step - loss: 0.8089
Epoch 6/100
50/50 [==============================] - 0s 40us/step - loss: 0.8057
Epoch 7/100
50/50 [==============================] - 0s 60us/step - loss: 0.8019
Epoch 8/100
50/50 [==============================] - 0s 60us/step - loss: 0.7977
Epoch 9/100
50/50 [==============================] - 0s 60us/step - loss: 0.7933
Epoch 10/100
50/50 [==============================] - 0s 40us/step - loss: 0.7886
Epoch 11/100
50/50 [==============================] - 0s 40us/step - loss: 0.7839
Epoch 12/100
50/50 [==============================] - 0s 20us/step - loss: 0.7791
Epoch 13/100
50/50 [======



                             Variable        eq0       eq1
0                   Volume_pct_change  -0.362833  0.021911
1              Volume_auto_pct_change  -0.094138  0.040996
2               Close_fmcg_pct_change   6.810985 -0.132297
3                 Close_it_pct_change  10.134008 -0.514739
4                Volume_it_pct_change  -0.426177 -0.221359
5                Low_media_pct_change   4.837937 -0.437494
6             Volume_media_pct_change   0.889021  0.158240
7            Volume_pharma_pct_change  -0.270360 -0.096133
8          Turnover_realty_pct_change  -1.179662 -0.237516
9                      return_2d_fmcg   3.303756 -0.491422
10                       return_2d_it  -6.094837  0.019523
11                       return_5d_it  12.446659 -0.382403
12                    return_1d_media  -3.658533  0.408549
13                    return_3d_media   7.621752 -0.201879
14                    return_4d_media  -4.175169  0.145618
15                   return_1d_pharma  -5.794254  0.59

Epoch 73/100
50/50 [==============================] - 0s 60us/step - loss: 0.6227
Epoch 74/100
50/50 [==============================] - 0s 60us/step - loss: 0.6214
Epoch 75/100
50/50 [==============================] - 0s 60us/step - loss: 0.6200
Epoch 76/100
50/50 [==============================] - 0s 40us/step - loss: 0.6187
Epoch 77/100
50/50 [==============================] - 0s 40us/step - loss: 0.6173
Epoch 78/100
50/50 [==============================] - 0s 40us/step - loss: 0.6160
Epoch 79/100
50/50 [==============================] - 0s 40us/step - loss: 0.6147
Epoch 80/100
50/50 [==============================] - 0s 20us/step - loss: 0.6133
Epoch 81/100
50/50 [==============================] - 0s 40us/step - loss: 0.6120
Epoch 82/100
50/50 [==============================] - 0s 40us/step - loss: 0.6107
Epoch 83/100
50/50 [==============================] - 0s 40us/step - loss: 0.6094
Epoch 84/100
50/50 [==============================] - 0s 20us/step - loss: 0.6081
Epoch 85/100
50/

Epoch 40/100
50/50 [==============================] - 0s 40us/step - loss: 0.4573
Epoch 41/100
50/50 [==============================] - 0s 40us/step - loss: 0.4559
Epoch 42/100
50/50 [==============================] - 0s 60us/step - loss: 0.4546
Epoch 43/100
50/50 [==============================] - 0s 40us/step - loss: 0.4533
Epoch 44/100
50/50 [==============================] - 0s 60us/step - loss: 0.4520
Epoch 45/100
50/50 [==============================] - 0s 60us/step - loss: 0.4507
Epoch 46/100
50/50 [==============================] - 0s 40us/step - loss: 0.4494
Epoch 47/100
50/50 [==============================] - 0s 40us/step - loss: 0.4482
Epoch 48/100
50/50 [==============================] - 0s 60us/step - loss: 0.4469
Epoch 49/100
50/50 [==============================] - 0s 40us/step - loss: 0.4457
Epoch 50/100
50/50 [==============================] - 0s 60us/step - loss: 0.4445
Epoch 51/100
50/50 [==============================] - 0s 279us/step - loss: 0.4433
Epoch 52/100
50

...

Epoch 100/100
50/50 [==============================] - 0s 259us/step - loss: 0.4745


                             Variable        eq0       eq1       eq2  \
0                   Volume_pct_change  -0.362833  0.021911  0.219635   
1              Volume_auto_pct_change  -0.094138  0.040996 -0.047180   
2               Close_fmcg_pct_change   6.810985 -0.132297  0.937743   
3                 Close_it_pct_change  10.134008 -0.514739  0.857091   
4                Volume_it_pct_change  -0.426177 -0.221359  0.151262   
5                Low_media_pct_change   4.837937 -0.437494  0.714338   
6             Volume_media_pct_change   0.889021  0.158240 -0.071330   
7            Volume_pharma_pct_change  -0.270360 -0.096133  0.679036   
8          Turnover_realty_pct_change  -1.179662 -0.237516  0.028014   
9                      return_2d_fmcg   3.303756 -0.491422  1.156637   
10                       return_2d_it  -6.094837  0.019523  0.195842   
11                       return_5d_it  12.446659 -

Epoch 1/100
50/50 [==============================] - 1s 27ms/step - loss: 0.8769
Epoch 2/100
50/50 [==============================] - 0s 219us/step - loss: 0.8742
Epoch 3/100
50/50 [==============================] - 0s 239us/step - loss: 0.8685
Epoch 4/100
50/50 [==============================] - 0s 319us/step - loss: 0.8603
Epoch 5/100
50/50 [==============================] - 0s 618us/step - loss: 0.8502
Epoch 6/100
50/50 [==============================] - 0s 279us/step - loss: 0.8386
Epoch 7/100
50/50 [==============================] - 0s 279us/step - loss: 0.8261
Epoch 8/100
50/50 [==============================] - 0s 319us/step - loss: 0.8131
Epoch 9/100
50/50 [==============================] - 0s 299us/step - loss: 0.7999
Epoch 10/100
50/50 [==============================] - 0s 379us/step - loss: 0.7868
Epoch 11/100
50/50 [==============================] - 0s 259us/step - loss: 0.7740
Epoch 12/100
50/50 [==============================] - 0s 578us/step - loss: 0.7618
Epoch 13/100
5

Epoch 100/100
50/50 [==============================] - 0s 219us/step - loss: 0.5711


                             Variable        eq0       eq1       eq2  \
0                   Volume_pct_change  -0.362833  0.021911  0.219635   
1              Volume_auto_pct_change  -0.094138  0.040996 -0.047180   
2               Close_fmcg_pct_change   6.810985 -0.132297  0.937743   
3                 Close_it_pct_change  10.134008 -0.514739  0.857091   
4                Volume_it_pct_change  -0.426177 -0.221359  0.151262   
5                Low_media_pct_change   4.837937 -0.437494  0.714338   
6             Volume_media_pct_change   0.889021  0.158240 -0.071330   
7            Volume_pharma_pct_change  -0.270360 -0.096133  0.679036   
8          Turnover_realty_pct_change  -1.179662 -0.237516  0.028014   
9                      return_2d_fmcg   3.303756 -0.491422  1.156637   
10                       return_2d_it  -6.094837  0.019523  0.195842   
11                       return_5d_it  12.446659 -

Epoch 1/100
50/50 [==============================] - 1s 24ms/step - loss: 0.8018
Epoch 2/100
50/50 [==============================] - 0s 239us/step - loss: 0.8009
Epoch 3/100
50/50 [==============================] - 0s 180us/step - loss: 0.7984
Epoch 4/100
50/50 [==============================] - 0s 299us/step - loss: 0.7946
Epoch 5/100
50/50 [==============================] - 0s 299us/step - loss: 0.7896
Epoch 6/100
50/50 [==============================] - 0s 259us/step - loss: 0.7839
Epoch 7/100
50/50 [==============================] - 0s 299us/step - loss: 0.7775
Epoch 8/100
50/50 [==============================] - 0s 339us/step - loss: 0.7706
Epoch 9/100
50/50 [==============================] - 0s 259us/step - loss: 0.7634
Epoch 10/100
50/50 [==============================] - 0s 259us/step - loss: 0.7561
Epoch 11/100
50/50 [==============================] - 0s 359us/step - loss: 0.7488
Epoch 12/100
50/50 [==============================] - 0s 379us/step - loss: 0.7415
Epoch 13/100
5

Epoch 100/100
50/50 [==============================] - 0s 219us/step - loss: 0.5304


                             Variable        eq0       eq1       eq2  \
0                   Volume_pct_change  -0.362833  0.021911  0.219635   
1              Volume_auto_pct_change  -0.094138  0.040996 -0.047180   
2               Close_fmcg_pct_change   6.810985 -0.132297  0.937743   
3                 Close_it_pct_change  10.134008 -0.514739  0.857091   
4                Volume_it_pct_change  -0.426177 -0.221359  0.151262   
5                Low_media_pct_change   4.837937 -0.437494  0.714338   
6             Volume_media_pct_change   0.889021  0.158240 -0.071330   
7            Volume_pharma_pct_change  -0.270360 -0.096133  0.679036   
8          Turnover_realty_pct_change  -1.179662 -0.237516  0.028014   
9                      return_2d_fmcg   3.303756 -0.491422  1.156637   
10                       return_2d_it  -6.094837  0.019523  0.195842   
11                       return_5d_it  12.446659 -

In [46]:
len(dates)

183

In [47]:
os.chdir('../Statistics/')

In [51]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
dynamic_eqn.to_excel(writer,sheet_name='ann_prob_dyn_eqn_lr',index=False)
writer.save()
writer.close()

In [48]:
ann_val_stats['month'] = ann_val_stats['Date'].apply(lambda x : str(x)[5:7])
ann_val_stats['year'] = ann_val_stats['Date'].apply(lambda x: str(x)[0:4])

In [53]:
ann_val_stats

Date      Symbol                  Sector  lift  lift_prob month  \
0     2019-01-01  ADANIPORTS     Services - Shipping     1   0.468341    01   
62    2019-01-01  ASIANPAINT          Consumer Goods     0   0.490655    01   
124   2019-01-01    AXISBANK                 Banking     1   0.486281    01   
186   2019-01-01  BAJAJ-AUTO              Automobile     0   0.465237    01   
248   2019-01-01  BAJFINANCE      Financial Services     1   0.477866    01   
310   2019-01-01  BAJAJFINSV      Financial Services     1   0.480555    01   
372   2019-01-01  BHARTIARTL       Telecommunication     1   0.492461    01   
434   2019-01-01    INFRATEL       Telecommunication     1   0.490911    01   
496   2019-01-01        BPCL      Energy - Oil & Gas     1   0.464706    01   
558   2019-01-01   BRITANNIA          Consumer Goods     0   0.484355    01   
620   2019-01-01       CIPLA         Pharmaceuticals     1   0.463799    01   
682   2019-01-01   COALINDIA                  Metals     1   0.481511    01   
744   2019-01-01     DRREDDY         Pharmaceuticals     0   0.460417    01   
806   2019-01-01   EICHERMOT              Automobile     1   0.461999    01   
868   2019-01-01        GAIL      Energy - Oil & Gas     1   0.460325    01   
930   2019-01-01      GRASIM                  Cement     1   0.488160    01   
992   2019-01-01     HCLTECH  Information Technology     0   0.492854    01   
1054  2019-01-01        HDFC      Financial Services     1   0.479904    01   
1116  2019-01-01    HDFCBANK                 Banking     1   0.486266    01   
1178  2019-01-01  HEROMOTOCO              Automobile     1   0.469671    01   
1240  2019-01-01    HINDALCO                  Metals     0   0.462518    01   
1302  2019-01-01  HINDUNILVR          Consumer Goods     0   0.487746    01   
1364  2019-01-01   ICICIBANK                 Banking     1   0.486136    01   
1426  2019-01-01  IBULHSGFIN      Financial Services     0   0.477069    01   
1488  2019-01-01  INDUSINDBK                 Banking     0   0.480076    01   
1550  2019-01-01        INFY  Information Technology     1   0.498176    01   
1612  2019-01-01         IOC      Energy - Oil & Gas     1   0.469414    01   
1674  2019-01-01         ITC          Consumer Goods     1   0.489935    01   
1736  2019-01-01    JSWSTEEL                  Metals     0   0.452083    01   
1798  2019-01-01   KOTAKBANK                 Banking     0   0.475174    01   
...          ...         ...                     ...   ...        ...   ...   
1301  2019-03-29    HINDALCO                  Metals     0   0.729350    03   
1363  2019-03-29  HINDUNILVR          Consumer Goods     1   0.796589    03   
1425  2019-03-29   ICICIBANK                 Banking     0   0.969826    03   
1487  2019-03-29  IBULHSGFIN      Financial Services     1   0.811783    03   
1549  2019-03-29  INDUSINDBK                 Banking     0   0.974317    03   
1611  2019-03-29        INFY  Information Technology     0   0.769636    03   
1673  2019-03-29         IOC      Energy - Oil & Gas     0   0.648272    03   
1735  2019-03-29         ITC          Consumer Goods     0   0.671339    03   
1797  2019-03-29    JSWSTEEL                  Metals     1   0.586852    03   
1859  2019-03-29   KOTAKBANK                 Banking     0   0.969521    03   
1921  2019-03-29          LT            Construction     0   0.602873    03   
1983  2019-03-29         M&M              Automobile     1   0.413579    03   
2045  2019-03-29      MARUTI              Automobile     1   0.468530    03   
2107  2019-03-29        NTPC          Energy - Power     0   0.333772    03   
2169  2019-03-29        ONGC      Energy - Oil & Gas     1   0.665192    03   
2231  2019-03-29   POWERGRID          Energy - Power     0   0.423146    03   
2293  2019-03-29    RELIANCE      Energy - Oil & Gas     0   0.750484    03   
2355  2019-03-29        SBIN                 Banking     0   0.948808    03   
2417  2019-03-29   SUNPHARMA         Pharmaceuticals     1   0

In [50]:
ann_val_stats = ann_val_stats[(ann_val_stats['Date'] >= '2019-04-01') & (ann_val_stats['Date'] <= '2019-12-31')]

In [51]:
ann_val_grp1 = ann_val_stats.groupby(['month','year','Symbol','Sector']).apply(lambda group : roc_auc_score(y_true=group.lift,
                                                                                                           y_score=group.lift_prob))

In [52]:
ann_val_grp1

month  year  Symbol      Sector                
04     2019  ADANIPORTS  Services - Shipping       0.512821
             ASIANPAINT  Consumer Goods            0.715909
             AXISBANK    Banking                   0.683333
             BAJAJ-AUTO  Automobile                0.633333
             BAJAJFINSV  Financial Services        0.309524
             BAJFINANCE  Financial Services        0.522727
             BHARTIARTL  Telecommunication         0.488889
             BPCL        Energy - Oil & Gas        0.633333
             BRITANNIA   Consumer Goods            0.769231
             CIPLA       Pharmaceuticals           0.522222
             COALINDIA   Metals                    0.440476
             DRREDDY     Pharmaceuticals           0.511364
             EICHERMOT   Automobile                0.566667
             GAIL        Energy - Oil & Gas        0.655556
             GRASIM      Cement                    0.420455
             HCLTECH     Information Technology    0

In [53]:
ann_val_grp2 = ann_val_stats.groupby(['month','year','Symbol','Sector']).agg({'lift':['count','sum']})

In [54]:
ann_val_grp2

lift    
                                             count sum
month year Symbol     Sector                          
04    2019 ADANIPORTS Services - Shipping       19  13
           ASIANPAINT Consumer Goods            19   8
           AXISBANK   Banking                   19   4
           BAJAJ-AUTO Automobile                19   9
           BAJAJFINSV Financial Services        19  12
           BAJFINANCE Financial Services        19   8
           BHARTIARTL Telecommunication         19   9
           BPCL       Energy - Oil & Gas        19   9
           BRITANNIA  Consumer Goods            19   6
           CIPLA      Pharmaceuticals           19   9
           COALINDIA  Metals                    19   7
           DRREDDY    Pharmaceuticals           19   8
           EICHERMOT  Automobile                19   9
           GAIL       Energy - Oil & Gas        19  10
           GRASIM     Cement                    19  11
           HCLTECH    Information Technology    19   8
           HDFC       Financial Services        19  10
           HDFCBANK   Banking                   19   9
           HEROMOTOCO Automobile                19   7
           HINDALCO   Metals                    19  11
           HINDUNILVR Consumer Goods            19  10
           IBULHSGFIN Financial Services        19   5
           ICICIBANK  Banking                   19   7
           INDUSINDBK Banking                   19   7
           INFRATEL   Telecommunication         19   7
           INFY       Information Technology    19  11
           IOC        Energy - Oil & Gas        19   9
           ITC        Consumer Goods            19   8
           JSWSTEEL   Metals                    19   7
           KOTAKBANK  Banking                   19  11
...                                            ...  ..
12    2019 HINDUNILVR Consumer Goods            21   6
           IBULHSGFIN Financial Services        21   9
           ICICIBANK  Banking                   21   9
           INDUSINDBK Banking                   21   8
           INFRATEL   Telecommunication         21   8
           INFY       Information Technology    21  14
           IOC        Energy - Oil & Gas        21   9
           ITC        Consumer Goods            21   7
           JSWSTEEL   Metals                    21  13
           KOTAKBANK  Banking                   21  12
           LT         Construction              21   9
           M&M        Automobile                21  10
           MARUTI     Automobile                21   6
           NTPC       Energy - Power            21  11
           ONGC       Energy - Oil & Gas        21   8
           POWERGRID  Energy - Power            21  11
           RELIANCE   Energy - Oil & Gas        21   8
           SBIN       Banking                   21   7
           SUNPHARMA  Pharmaceuticals           21  12
           TATAMOTORS Automobile                21   9
           TATASTEEL  Metals                    21  14
           TCS        Information Technology    21  10
           TECHM      Information Technology    21   8
           TITAN      Consumer Goods            21  10
           ULTRACEMCO Cement                    21   4
           UPL        Chemicals                 21   8
           VEDL       Metals                    21  10
           WIPRO      Information Technology    21  11
           YESBANK    Banking                   21   8
           ZEEL       Media & Entertainment     21  11

[450 rows x 2 columns]

In [55]:
ann_val_grp = pd.DataFrame(ann_val_grp1).join(ann_val_grp2)

C:\Users\DELL\Anaconda3\lib\site-packages\pandas\core\reshape\merge.py:543: UserWarning: merging between different levels can give an unintended result (1 levels on the left, 2 on the right)
  warnings.warn(msg, UserWarning)


In [56]:
ann_val_grp.columns = ['roc_auc_score','trade days','lifts']

In [57]:
ann_val_grp = ann_val_grp[['trade days','lifts','roc_auc_score']]

In [58]:
ann_val_grp.reset_index(inplace=True)

In [59]:
ann_val_grp.shape

(450, 7)

In [60]:
os.getcwd()

'C:\\Users\\DELL\\Desktop\\Trading App\\Revised_Investing\\Trading App_v02\\Price Prediction\\Statistics'

In [61]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
ann_val_grp.to_excel(writer,sheet_name='ann_prob_oot_stats_lr',index=False)
writer.save()
writer.close()

In [62]:
os.chdir('../Models/')

In [63]:
model.save('ann_prob_model_lr.h5')